In [1]:
'''
In this file we train SketchVAE + SketchInpainter
'''
import torch
import os
import numpy as np
from torch import optim
from torch.nn import functional as F
from SketchVAE.sketchvae import SketchVAE
from torch import optim
from torch.utils.data import Dataset, DataLoader, TensorDataset
from torch.distributions import Normal
from SketchNet.sketchnet import SketchNet
from utils.helpers import *
import time
###############################
# initial parameters
s_dir = "" # folder_address
zp_dims = 128
zr_dims = 128
pf_dims = 512
gen_dims = 1024
combine_dims = 512
combine_head = 4
combine_num = 4
pf_num = 2
inpaint_len = 4
total_len = 16
batch_size = 32
n_epochs = 100
save_path = "model_backup"
# set here to config your save_period (2 i.e. save the model every 2 epochs)
save_period = 5

"""
The same to 3-2
"""
data_path = [
    "data/irish-dis-measure-vae-train-whole.npy",
    "data/irish-dis-measure-vae-validate-whole.npy",
    "data/irish-dis-measure-vae-test-whole.npy"
]
lr = 1e-4
decay = 0.9999
##############################
##############  for vae init ##############
vae_hidden_dims = 1024
vae_zp_dims = 128
vae_zr_dims = 128
vae_beta = 0.1
vae_input_dims = 130
vae_pitch_dims = 129
vae_rhythm_dims = 3
vae_seq_len = 6 * 4
vae_beat_num = 4
vae_tick_num = 6
############################



In [2]:
# input data dis-measure-vae
def processed_data_tensor(data):
    print("processed data:")
    gd = [] 
    px = []
    rx = []
    len_x = []
    nrx = []
    total = 0
    for i, d in enumerate(data):
        gd.append([list(dd[0]) for dd in d])
        px.append([list(dd[1]) for dd in d])
        rx.append([list(dd[2]) for dd in d])
        len_x.append([dd[3] for dd in d])
        if len(gd[-1][-1]) != vae_seq_len:
            gd[-1][-1].extend([128] * (vae_seq_len - len(gd[-1][-1])))
            px[-1][-1].extend([128] * (vae_seq_len - len(px[-1][-1])))
            rx[-1][-1].extend([2] * (vae_seq_len - len(rx[-1][-1])))
    for i,d in enumerate(len_x):
        for j,dd in enumerate(d):
            if len_x[i][j] == 0:
                gd[i][j][0] = 60
                px[i][j][0] = 60
                rx[i][j][0] = 1
                len_x[i][j] = 1
                total += 1
    gd = np.array(gd)
    px = np.array(px)
    rx = np.array(rx)
    len_x = np.array(len_x)
    for d in rx:
        nnrx = []
        for dd in d:
            temp = np.zeros((vae_seq_len, vae_rhythm_dims))
            lins = np.arange(0, len(dd))
            temp[lins, dd - 1] = 1
            nnrx.append(temp)
        nrx.append(nnrx)
    nrx = np.array(nrx)
    gd = torch.from_numpy(gd).long()
    px = torch.from_numpy(px).long()
    rx = torch.from_numpy(rx).float()
    len_x = torch.from_numpy(len_x).long()
    nrx = torch.from_numpy(nrx).float()
    print("processed finish! zeros:", total)
    print(gd.size(),px.size(),rx.size(),len_x.size(),nrx.size())
    return TensorDataset(px, rx, len_x, nrx, gd)

train_set = np.load(os.path.join(s_dir,data_path[0]),allow_pickle = True)
train_loader = DataLoader(
    dataset = processed_data_tensor(train_set),
    batch_size = batch_size, 
    shuffle = True, 
    num_workers = 8, 
    pin_memory = True, 
    drop_last = True
)

validate_set = np.load(os.path.join(s_dir,data_path[1]),allow_pickle = True)
validate_loader = DataLoader(
    dataset = processed_data_tensor(validate_set),
    batch_size = batch_size, 
    shuffle = False, 
    num_workers = 8, 
    pin_memory = True, 
    drop_last = True
)
validate_data = []
for i,d in enumerate(validate_loader):
    validate_data.append(d)
print(len(validate_data))

processed data:
processed finish! zeros: 256
torch.Size([39798, 16, 24]) torch.Size([39798, 16, 24]) torch.Size([39798, 16, 24]) torch.Size([39798, 16]) torch.Size([39798, 16, 24, 3])
processed data:
processed finish! zeros: 1
torch.Size([2927, 16, 24]) torch.Size([2927, 16, 24]) torch.Size([2927, 16, 24]) torch.Size([2927, 16]) torch.Size([2927, 16, 24, 3])
91


In [3]:
# load VAE model
vae_model = SketchVAE(
    vae_input_dims, vae_pitch_dims, vae_rhythm_dims, vae_hidden_dims, 
    vae_zp_dims, vae_zr_dims, vae_seq_len, vae_beat_num, vae_tick_num, 4000)

# sketchvae-param.pt is your saved sketchVAE model
dic = torch.load(os.path.join(s_dir, save_path, "sketchvae-param.pt"))

for name in list(dic.keys()):
    dic[name.replace('module.', '')] = dic.pop(name)
vae_model.load_state_dict(dic)

if torch.cuda.is_available():
    print('Using: ', torch.cuda.get_device_name(torch.cuda.current_device()))
    vae_model.cuda()
else:
    print('Using: CPU')
vae_model.eval()
print(vae_model.training)

Using:  Tesla V100-SXM2-32GB
False


In [4]:
# import model
model = SketchNet(
    zp_dims, zr_dims, 
    pf_dims, gen_dims, combine_dims,
    pf_num, combine_num, combine_head,
    inpaint_len, total_len, 
    vae_model, True
)
optimizer = optim.Adam(filter(lambda p: p.requires_grad, model.parameters()),lr=lr)
if torch.cuda.is_available():
    print('Using: ', torch.cuda.get_device_name(torch.cuda.current_device()))
    model.cuda()
else:
    print('Using: CPU')
print(model)

Using:  Tesla V100-SXM2-32GB
SketchNet(
  (past_p_gru): GRU(128, 512, num_layers=2, batch_first=True, dropout=0.5, bidirectional=True)
  (past_r_gru): GRU(128, 512, num_layers=2, batch_first=True, dropout=0.5, bidirectional=True)
  (future_p_gru): GRU(128, 512, num_layers=2, batch_first=True, dropout=0.5, bidirectional=True)
  (future_r_gru): GRU(128, 512, num_layers=2, batch_first=True, dropout=0.5, bidirectional=True)
  (gen_p_gru): GRU(128, 1024, num_layers=2, batch_first=True, dropout=0.5, bidirectional=True)
  (gen_r_gru): GRU(128, 1024, num_layers=2, batch_first=True, dropout=0.5, bidirectional=True)
  (gen_p_out): Linear(in_features=2048, out_features=128, bias=True)
  (gen_r_out): Linear(in_features=2048, out_features=128, bias=True)
  (combine_in): Linear(in_features=256, out_features=512, bias=True)
  (combine_posenc): PositionalEncoding()
  (combine_dropout): Dropout(p=0.1, inplace=False)
  (combine_nn): ModuleList(
    (0): CombineLayer(
      (slf_attn): MultiHeadAttention

In [ ]:
def process_raw_x(raw_x, n_past, n_inpaint, n_future):
    raw_px, raw_rx, raw_len_x, raw_nrx, raw_gd = raw_x
    past_px = raw_px[:,:n_past,:]
    inpaint_px = raw_px[:,n_past:n_past + n_inpaint,:]
    future_px = raw_px[:,n_future:,:]
    past_rx = raw_rx[:,:n_past,:]
    inpaint_rx = raw_rx[:,n_past:n_past + n_inpaint,:]
    future_rx = raw_rx[:,n_future:,:]
    past_len_x = raw_len_x[:,:n_past]
    inpaint_len_x = raw_len_x[:,n_past:n_past + n_inpaint]
    future_len_x = raw_len_x[:,n_future:]
    past_nrx = raw_nrx[:,:n_past,:]
    inpaint_nrx = raw_nrx[:,n_past:n_past + n_inpaint,:]
    future_nrx = raw_nrx[:,n_future:,:]
    past_gd = raw_gd[:,:n_past,:]
    inpaint_gd = raw_gd[:,n_past:n_past + n_inpaint,:]
    future_gd = raw_gd[:,n_future:,:]
    re = [
        past_px, past_rx, past_len_x, past_nrx, past_gd,
        inpaint_px, inpaint_rx, inpaint_len_x, inpaint_nrx, inpaint_gd,
        future_px, future_rx, future_len_x, future_nrx, future_gd,
    ]
    return re
def get_acc(recon, gd):
    recon = recon.cpu().detach().numpy()
    gd = gd.cpu().detach().numpy()
    return np.sum(recon == gd) / recon.size

model.set_stage = "inpainting"
device = torch.device(torch.cuda.current_device())
losses = []
step = 0
n_past = 6
n_future = 10
n_inpaint = 4
iteration = 0
# save_period = 200
print(vae_model.training)
for epoch in range(n_epochs):
    model.train()
    print("epoch: %d\n__________________________________________" % (epoch), flush = True)
    mean_loss = 0.0
    mean_acc = 0.0
    v_mean_loss = 0.0
    v_mean_acc = 0.0
    total = 0
    for i,tr_data in enumerate(train_loader):
        model.train()
#         print("begin_time", time.process_time())
        j = i % len(validate_data)
        raw_x = process_raw_x(tr_data, n_past, n_inpaint, n_future)
        for k in range(len(raw_x)):
            raw_x[k] = raw_x[k].to(device = device,non_blocking = True)
        past_px, past_rx, past_len_x, past_nrx, past_gd, \
        inpaint_px, inpaint_rx, inpaint_len_x, inpaint_nrx, inpaint_gd,\
        future_px, future_rx, future_len_x, future_nrx, future_gd = raw_x
        inpaint_gd_whole = inpaint_gd.contiguous().view(-1)
        past_x = [past_px, past_rx, past_len_x, past_nrx, past_gd]
        inpaint_x = [inpaint_px, inpaint_rx, inpaint_len_x, inpaint_nrx, inpaint_gd]
        future_x = [future_px, future_rx, future_len_x, future_nrx, future_gd]
        
        # validate
        v_raw_x = process_raw_x(validate_data[j], n_past, n_inpaint, n_future)
        for k in range(len(v_raw_x)):
            v_raw_x[k] = v_raw_x[k].to(device = device,non_blocking = True)
        v_past_px, v_past_rx, v_past_len_x, v_past_nrx, v_past_gd, \
        v_inpaint_px, v_inpaint_rx, v_inpaint_len_x, v_inpaint_nrx, v_inpaint_gd,\
        v_future_px, v_future_rx, v_future_len_x, v_future_nrx, v_future_gd = v_raw_x
        v_inpaint_gd_whole = v_inpaint_gd.contiguous().view(-1)
        v_past_x = [v_past_px, v_past_rx, v_past_len_x, v_past_nrx, v_past_gd]
        v_inpaint_x = [v_inpaint_px, v_inpaint_rx, v_inpaint_len_x, v_inpaint_nrx, v_inpaint_gd]
        v_future_x = [v_future_px, v_future_rx, v_future_len_x, v_future_nrx, v_future_gd]
        
        optimizer.zero_grad()
        
        recon_x, iteration, use_teacher, stage = model(past_x, future_x, inpaint_x)

        loss = F.cross_entropy(recon_x.view(-1, recon_x.size(-1)), inpaint_gd_whole, reduction = "mean") 
        acc = get_acc(recon_x.view(-1, recon_x.size(-1)).argmax(-1), inpaint_gd_whole)
        loss.backward()
        optimizer.step()
   
        total += 1
        mean_loss += loss.item()
        mean_acc += acc
  
        model.eval()
        with torch.no_grad():
            v_recon_x, _,_,_ = model(v_past_x, v_future_x, v_inpaint_x)
            v_loss = F.cross_entropy(v_recon_x.view(-1, v_recon_x.size(-1)), v_inpaint_gd_whole, reduction = "mean") 
            v_acc = get_acc(v_recon_x.view(-1, v_recon_x.size(-1)).argmax(-1), v_inpaint_gd_whole)
            v_mean_loss += v_loss.item()
            v_mean_acc += v_acc
        print("batch %d loss: %.5f acc: %.5f | v_loss: %.5f v_acc: %.5f |  iteration: %d teacher: %d stage: %s" \
              % (i,loss.item(), acc, v_loss.item(), v_acc, iteration, use_teacher, stage),flush = True)
    mean_loss /= total
    mean_acc /= total
    v_mean_loss /= total
    v_mean_acc /= total
    print("epoch %d loss: %.5f acc: %.5f | v_loss: %.5f v_acc: %.5f "  % (epoch,mean_loss, mean_acc, v_mean_loss, v_mean_acc),flush = True)
    losses.append([mean_loss, v_mean_loss])
    if (epoch + 1) % save_period == 0:
        filename = "sketchNet-stage-1" + 'loss_' + str(v_mean_loss) + "_acc_" + str(v_mean_acc) + "_epoch_" + str(epoch+1) + '_it_' + str(iteration) + ".pt"
        torch.save(model.cpu().state_dict(),os.path.join(s_dir, save_path, filename))
        model.cuda()
    np.save(os.path.join(s_dir,"sketchnet_stage1_log.npy"),losses)


False
epoch: 0
__________________________________________
batch 0 loss: 3.43902 acc: 0.65397 | v_loss: 2.84543 v_acc: 0.66960 |  iteration: 1 teacher: 1 stage: inpainting
batch 1 loss: 2.92011 acc: 0.66667 | v_loss: 2.65966 v_acc: 0.67839 |  iteration: 2 teacher: 0 stage: inpainting
batch 2 loss: 2.94030 acc: 0.67285 | v_loss: 2.94139 v_acc: 0.66992 |  iteration: 3 teacher: 1 stage: inpainting
batch 3 loss: 2.89193 acc: 0.67285 | v_loss: 2.51503 v_acc: 0.68392 |  iteration: 4 teacher: 1 stage: inpainting
batch 4 loss: 2.92443 acc: 0.66439 | v_loss: 2.54684 v_acc: 0.67773 |  iteration: 5 teacher: 1 stage: inpainting
batch 5 loss: 2.69071 acc: 0.68132 | v_loss: 2.27200 v_acc: 0.68359 |  iteration: 6 teacher: 1 stage: inpainting
batch 6 loss: 2.47258 acc: 0.69043 | v_loss: 2.51808 v_acc: 0.68490 |  iteration: 7 teacher: 1 stage: inpainting
batch 7 loss: 2.37679 acc: 0.69303 | v_loss: 2.92275 v_acc: 0.66341 |  iteration: 8 teacher: 0 stage: inpainting
batch 8 loss: 2.44520 acc: 0.69336 | v

batch 71 loss: 1.89953 acc: 0.67285 | v_loss: 1.71649 v_acc: 0.67871 |  iteration: 72 teacher: 0 stage: inpainting
batch 72 loss: 1.86513 acc: 0.68294 | v_loss: 1.85627 v_acc: 0.67611 |  iteration: 73 teacher: 1 stage: inpainting
batch 73 loss: 1.73364 acc: 0.68555 | v_loss: 1.71121 v_acc: 0.69857 |  iteration: 74 teacher: 0 stage: inpainting
batch 74 loss: 1.85383 acc: 0.68880 | v_loss: 1.67960 v_acc: 0.69857 |  iteration: 75 teacher: 0 stage: inpainting
batch 75 loss: 1.75069 acc: 0.68652 | v_loss: 1.68980 v_acc: 0.68652 |  iteration: 76 teacher: 1 stage: inpainting
batch 76 loss: 1.82480 acc: 0.67546 | v_loss: 1.70539 v_acc: 0.68717 |  iteration: 77 teacher: 0 stage: inpainting
batch 77 loss: 1.68299 acc: 0.69661 | v_loss: 1.61197 v_acc: 0.69694 |  iteration: 78 teacher: 1 stage: inpainting
batch 78 loss: 1.74563 acc: 0.68262 | v_loss: 1.95097 v_acc: 0.66309 |  iteration: 79 teacher: 0 stage: inpainting
batch 79 loss: 1.77998 acc: 0.68197 | v_loss: 1.67370 v_acc: 0.68978 |  iteratio

batch 142 loss: 1.58316 acc: 0.71094 | v_loss: 1.44835 v_acc: 0.71680 |  iteration: 143 teacher: 1 stage: inpainting
batch 143 loss: 1.58820 acc: 0.69954 | v_loss: 1.59971 v_acc: 0.70768 |  iteration: 144 teacher: 0 stage: inpainting
batch 144 loss: 1.69134 acc: 0.69564 | v_loss: 1.57909 v_acc: 0.70605 |  iteration: 145 teacher: 1 stage: inpainting
batch 145 loss: 1.60195 acc: 0.70931 | v_loss: 1.57887 v_acc: 0.70475 |  iteration: 146 teacher: 1 stage: inpainting
batch 146 loss: 1.62014 acc: 0.70280 | v_loss: 1.58028 v_acc: 0.70703 |  iteration: 147 teacher: 1 stage: inpainting
batch 147 loss: 1.55152 acc: 0.70736 | v_loss: 1.64301 v_acc: 0.71973 |  iteration: 148 teacher: 0 stage: inpainting
batch 148 loss: 1.63694 acc: 0.69792 | v_loss: 1.66395 v_acc: 0.69076 |  iteration: 149 teacher: 0 stage: inpainting
batch 149 loss: 1.57052 acc: 0.71061 | v_loss: 1.71512 v_acc: 0.70312 |  iteration: 150 teacher: 0 stage: inpainting
batch 150 loss: 1.59841 acc: 0.70671 | v_loss: 1.52995 v_acc: 0.

batch 213 loss: 1.56465 acc: 0.70996 | v_loss: 1.49028 v_acc: 0.70182 |  iteration: 214 teacher: 0 stage: inpainting
batch 214 loss: 1.50924 acc: 0.71387 | v_loss: 1.74439 v_acc: 0.69043 |  iteration: 215 teacher: 1 stage: inpainting
batch 215 loss: 1.49929 acc: 0.71908 | v_loss: 1.49353 v_acc: 0.70508 |  iteration: 216 teacher: 1 stage: inpainting
batch 216 loss: 1.46526 acc: 0.71842 | v_loss: 1.65472 v_acc: 0.69206 |  iteration: 217 teacher: 1 stage: inpainting
batch 217 loss: 1.54920 acc: 0.70736 | v_loss: 1.45006 v_acc: 0.72852 |  iteration: 218 teacher: 0 stage: inpainting
batch 218 loss: 1.49208 acc: 0.71484 | v_loss: 1.69504 v_acc: 0.68913 |  iteration: 219 teacher: 1 stage: inpainting
batch 219 loss: 1.64942 acc: 0.69531 | v_loss: 1.68480 v_acc: 0.69076 |  iteration: 220 teacher: 1 stage: inpainting
batch 220 loss: 1.55682 acc: 0.70573 | v_loss: 1.59819 v_acc: 0.69661 |  iteration: 221 teacher: 1 stage: inpainting
batch 221 loss: 1.56178 acc: 0.70638 | v_loss: 1.57276 v_acc: 0.

batch 284 loss: 1.46634 acc: 0.71777 | v_loss: 1.49774 v_acc: 0.71745 |  iteration: 285 teacher: 0 stage: inpainting
batch 285 loss: 1.59607 acc: 0.70736 | v_loss: 1.23570 v_acc: 0.75228 |  iteration: 286 teacher: 0 stage: inpainting
batch 286 loss: 1.48249 acc: 0.72168 | v_loss: 1.42885 v_acc: 0.72266 |  iteration: 287 teacher: 1 stage: inpainting
batch 287 loss: 1.55534 acc: 0.70931 | v_loss: 1.32562 v_acc: 0.74935 |  iteration: 288 teacher: 0 stage: inpainting
batch 288 loss: 1.52122 acc: 0.71582 | v_loss: 1.43076 v_acc: 0.72884 |  iteration: 289 teacher: 0 stage: inpainting
batch 289 loss: 1.48087 acc: 0.72363 | v_loss: 1.48051 v_acc: 0.72363 |  iteration: 290 teacher: 0 stage: inpainting
batch 290 loss: 1.42168 acc: 0.72721 | v_loss: 1.37049 v_acc: 0.72461 |  iteration: 291 teacher: 1 stage: inpainting
batch 291 loss: 1.46273 acc: 0.72266 | v_loss: 1.33109 v_acc: 0.73633 |  iteration: 292 teacher: 0 stage: inpainting
batch 292 loss: 1.45229 acc: 0.72363 | v_loss: 1.58566 v_acc: 0.

...

batch 192 loss: 0.31654 acc: 0.90202 | v_loss: 0.52733 v_acc: 0.86100 |  iteration: 68558 teacher: 0 stage: inpainting
batch 193 loss: 0.40683 acc: 0.87272 | v_loss: 0.60349 v_acc: 0.84505 |  iteration: 68559 teacher: 0 stage: inpainting
batch 194 loss: 0.41102 acc: 0.87370 | v_loss: 0.53581 v_acc: 0.86491 |  iteration: 68560 teacher: 0 stage: inpainting
batch 195 loss: 0.08186 acc: 0.97493 | v_loss: 0.47064 v_acc: 0.87207 |  iteration: 68561 teacher: 1 stage: inpainting
batch 196 loss: 0.09367 acc: 0.96810 | v_loss: 1.04578 v_acc: 0.77897 |  iteration: 68562 teacher: 1 stage: inpainting
batch 197 loss: 0.06875 acc: 0.97786 | v_loss: 0.40503 v_acc: 0.88672 |  iteration: 68563 teacher: 1 stage: inpainting
batch 198 loss: 0.39512 acc: 0.88021 | v_loss: 0.64824 v_acc: 0.84473 |  iteration: 68564 teacher: 0 stage: inpainting
batch 199 loss: 0.12301 acc: 0.96029 | v_loss: 0.56804 v_acc: 0.85840 |  iteration: 68565 teacher: 1 stage: inpainting
batch 200 loss: 0.46757 acc: 0.86361 | v_loss: 0

batch 261 loss: 0.37932 acc: 0.88932 | v_loss: 0.55485 v_acc: 0.85514 |  iteration: 68627 teacher: 0 stage: inpainting
batch 262 loss: 0.07085 acc: 0.97624 | v_loss: 0.57244 v_acc: 0.85677 |  iteration: 68628 teacher: 1 stage: inpainting
batch 263 loss: 0.08688 acc: 0.97168 | v_loss: 0.52039 v_acc: 0.85514 |  iteration: 68629 teacher: 1 stage: inpainting
batch 264 loss: 0.09067 acc: 0.97233 | v_loss: 0.49955 v_acc: 0.87207 |  iteration: 68630 teacher: 1 stage: inpainting
batch 265 loss: 0.11124 acc: 0.96517 | v_loss: 0.52208 v_acc: 0.86914 |  iteration: 68631 teacher: 1 stage: inpainting
batch 266 loss: 0.10142 acc: 0.96680 | v_loss: 0.65746 v_acc: 0.84017 |  iteration: 68632 teacher: 1 stage: inpainting
batch 267 loss: 0.34664 acc: 0.89290 | v_loss: 0.43567 v_acc: 0.87956 |  iteration: 68633 teacher: 0 stage: inpainting
batch 268 loss: 0.37592 acc: 0.88477 | v_loss: 0.95263 v_acc: 0.79362 |  iteration: 68634 teacher: 0 stage: inpainting
batch 269 loss: 0.10707 acc: 0.96908 | v_loss: 0

batch 330 loss: 0.40832 acc: 0.87760 | v_loss: 0.55827 v_acc: 0.84831 |  iteration: 68696 teacher: 0 stage: inpainting
batch 331 loss: 0.38626 acc: 0.87760 | v_loss: 0.85361 v_acc: 0.80957 |  iteration: 68697 teacher: 0 stage: inpainting
batch 332 loss: 0.08469 acc: 0.97428 | v_loss: 0.41450 v_acc: 0.88021 |  iteration: 68698 teacher: 1 stage: inpainting
batch 333 loss: 0.09738 acc: 0.96908 | v_loss: 0.36487 v_acc: 0.89225 |  iteration: 68699 teacher: 1 stage: inpainting
batch 334 loss: 0.10203 acc: 0.96745 | v_loss: 0.58580 v_acc: 0.85026 |  iteration: 68700 teacher: 1 stage: inpainting
batch 335 loss: 0.10507 acc: 0.96940 | v_loss: 0.63016 v_acc: 0.84831 |  iteration: 68701 teacher: 1 stage: inpainting
batch 336 loss: 0.09378 acc: 0.97266 | v_loss: 0.68532 v_acc: 0.83268 |  iteration: 68702 teacher: 1 stage: inpainting
batch 337 loss: 0.07235 acc: 0.97656 | v_loss: 0.49905 v_acc: 0.85905 |  iteration: 68703 teacher: 1 stage: inpainting
batch 338 loss: 0.09727 acc: 0.97005 | v_loss: 0

batch 399 loss: 0.09767 acc: 0.97005 | v_loss: 0.66147 v_acc: 0.83236 |  iteration: 68765 teacher: 1 stage: inpainting
batch 400 loss: 0.36020 acc: 0.89258 | v_loss: 0.53978 v_acc: 0.85872 |  iteration: 68766 teacher: 0 stage: inpainting
batch 401 loss: 0.37359 acc: 0.88184 | v_loss: 0.59413 v_acc: 0.83887 |  iteration: 68767 teacher: 0 stage: inpainting
batch 402 loss: 0.10835 acc: 0.96745 | v_loss: 0.63823 v_acc: 0.83887 |  iteration: 68768 teacher: 1 stage: inpainting
batch 403 loss: 0.52768 acc: 0.84505 | v_loss: 0.71451 v_acc: 0.82357 |  iteration: 68769 teacher: 0 stage: inpainting
batch 404 loss: 0.36331 acc: 0.89486 | v_loss: 0.61640 v_acc: 0.84733 |  iteration: 68770 teacher: 0 stage: inpainting
batch 405 loss: 0.11079 acc: 0.96777 | v_loss: 0.64974 v_acc: 0.84961 |  iteration: 68771 teacher: 1 stage: inpainting
batch 406 loss: 0.40799 acc: 0.87435 | v_loss: 0.63282 v_acc: 0.84766 |  iteration: 68772 teacher: 0 stage: inpainting
batch 407 loss: 0.08726 acc: 0.96908 | v_loss: 0

batch 468 loss: 0.40069 acc: 0.87630 | v_loss: 0.46822 v_acc: 0.86784 |  iteration: 68834 teacher: 0 stage: inpainting
batch 469 loss: 0.08657 acc: 0.97070 | v_loss: 1.04855 v_acc: 0.78906 |  iteration: 68835 teacher: 1 stage: inpainting
batch 470 loss: 0.09531 acc: 0.96745 | v_loss: 0.38481 v_acc: 0.89518 |  iteration: 68836 teacher: 1 stage: inpainting
batch 471 loss: 0.41147 acc: 0.88542 | v_loss: 0.65415 v_acc: 0.83919 |  iteration: 68837 teacher: 0 stage: inpainting
batch 472 loss: 0.09196 acc: 0.97168 | v_loss: 0.55369 v_acc: 0.86719 |  iteration: 68838 teacher: 1 stage: inpainting
batch 473 loss: 0.39834 acc: 0.87826 | v_loss: 0.46766 v_acc: 0.87695 |  iteration: 68839 teacher: 0 stage: inpainting
batch 474 loss: 0.40735 acc: 0.87402 | v_loss: 0.57203 v_acc: 0.85807 |  iteration: 68840 teacher: 0 stage: inpainting
batch 475 loss: 0.42456 acc: 0.86914 | v_loss: 0.60679 v_acc: 0.84570 |  iteration: 68841 teacher: 0 stage: inpainting
batch 476 loss: 0.09442 acc: 0.96745 | v_loss: 0